In [1]:
# Make output easier to read
from rich import pretty

pretty.install()

In [2]:
from quantify_scheduler.schemas.examples import utils

# load here to avoid loading every time a fixture is used
transmon_device_cfg = utils.load_json_example_scheme("transmon_test_config.json")
zhinst_hardware_cfg = utils.load_json_example_scheme("zhinst_test_mapping.json")

zhinst_hardware_cfg

{
    'backend': 'quantify_scheduler.backends.zhinst_backend.compile_backend',
    'mode': 'calibration',
    'latency_corrections': {
        'q0:mw-q0.01': 9.5e-08,
        'q1:mw-q1.01': 9.5e-08,
        'q0:res-q0.ro': -9.5e-08,
        'q1:res-q1.ro': -9.5e-08
    },
    'local_oscillators': [
        {
            'unique_name': 'mw_qubit_ch1',
            'instrument_name': 'mw_qubit',
            'frequency': {'ch_1.frequency': None},
            'power': {'power': 13}
        },
        {
            'unique_name': 'mw_qubit_ch2',
            'instrument_name': 'mw_qubit',
            'frequency': {'ch_2.frequency': None},
            'power': {'ch_2.power': 10}
        },
        {
            'unique_name': 'mw_readout',
            'instrument_name': 'mw_readout',
            'frequency': {'frequency': None},
            'power': {'power': 16}
        }
    ],
    'devices': [
        {
            'name': 'ic_hdawg0',
            'type': 'HDAWG4',
            'clock_select': 0,
            'ref': 'int',
            'channelgrouping': 0,
            'channel_0': {
                'port': 'q0:mw',
                'clock': 'q0.01',
                'mode': 'complex',
                'modulation': {'type': 'premod', 'interm_freq': -100000000.0},
                'local_oscillator': 'mw_qubit_ch1',
                'clock_frequency': 6000000000.0,
                'markers': ['AWG_MARKER1', 'AWG_MARKER2'],
                'gain1': 1,
                'gain2': 1,
                'mixer_corrections': {
                    'amp_ratio': 0.95,
                    'phase_error': 0.07,
                    'dc_offset_I': -0.0542,
                    'dc_offset_Q': -0.0328
                }
            },
            'channel_1': {
                'port': 'q1:mw',
                'clock': 'q1.01',
                'mode': 'complex',
                'modulation': {'type': 'premod', 'interm_freq': -100000000.0},
                'local_oscillator': 'mw_qubit_ch2',
                'clock_frequency': 6000000000.0,
                'markers': ['AWG_MARKER1', 'AWG_MARKER2'],
                'gain1': 1,
                'gain2': 1,
                'mixer_corrections': {
                    'amp_ratio': 0.95,
                    'phase_error': 0.07,
                    'dc_offset_I': 0.042,
                    'dc_offset_Q': 0.028
                }
            }
        },
        {
            'name': 'ic_uhfqa0',
            'type': 'UHFQA',
            'ref': 'ext',
            'channel_0': {
                'port': 'q0:res',
                'clock': 'q0.ro',
                'mode': 'real',
                'modulation': {'type': 'premod', 'interm_freq': 200000000.0},
                'local_oscillator': 'mw_readout',
                'clock_frequency': 6000000000.0,
                'trigger': 2
            }
        }
    ]
}

In [3]:
# import statements required to make a schedule

import numpy as np

from quantify_scheduler import Schedule
from quantify_scheduler.operations.acquisition_library import SSBIntegrationComplex
from quantify_scheduler.operations.pulse_library import IdlePulse, SquarePulse
from quantify_scheduler.resources import ClockResource

In [4]:
pulse_amps = np.linspace(0.05, 0.9, 3)
repetitions = 1024
init_duration = 4000e-6  # 4us should allow for plenty of wait time
mw_port = "q0:mw"
ro_port = "q0:res"
mw_clock = "q0.01"  # chosen to correspond to values in the hardware cfg
ro_clock = "q0.ro"
readout_frequency = (
    6.5e9  # this frequency will be used for both the AWG pulse as well as
)
# for the readout.

pulse_duration = 1e-6
acq_channel = 0
integration_time = 2e-6
acquisition_delay = 0


sched = Schedule(name="AWG staircase", repetitions=repetitions)

sched.add_resource(ClockResource(name=mw_clock, freq=readout_frequency))
sched.add_resource(ClockResource(name=ro_clock, freq=readout_frequency))
pulse_amps = np.asarray(pulse_amps)


for acq_index, pulse_amp in enumerate(pulse_amps):

    sched.add(IdlePulse(duration=init_duration))

    pulse = sched.add(
        SquarePulse(
            duration=pulse_duration,
            amp=pulse_amp,
            port=mw_port,
            clock=mw_clock,
        ),
        label=f"SquarePulse_{acq_index}",
    )

    sched.add(
        SSBIntegrationComplex(
            duration=integration_time,
            port=ro_port,
            clock=ro_clock,
            acq_index=acq_index,
            acq_channel=acq_channel,
        ),
        ref_op=pulse,
        ref_pt="start",
        rel_time=acquisition_delay,
        label=f"Acquisition_{acq_index}",
    )

sched

Schedule "AWG staircase" containing (7) 9  (unique) operations.

In [5]:
from quantify_scheduler.compilation import qcompile

comp_sched = qcompile(
    schedule=sched, device_cfg=transmon_device_cfg, hardware_cfg=zhinst_hardware_cfg
)

In [6]:
# Pandas dataframes do not render correctly in the sphinx documentation environment. See issue #238.
comp_sched.timing_table

waveform_op_id 
 port 
 clock 
 is_acquisition 
 abs_time 
 duration 
 operation 
 wf_idx 
 
 
 
 
 0 
 IdlePulse(duration=0.004)_p_0 
 None 
 cl0.baseband 
 False 
 0.0 ns 
 4,000,000.0 ns 
 IdlePulse(duration=0.004) 
 0 
 
 
 1 
 SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0 
 q0:mw 
 q0.01 
 False 
 4,000,000.0 ns 
 1,000.0 ns 
 SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0) 
 0 
 
 
 2 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=0,bin_mode='average',phase=0,t0=0)_acq_0 
 q0:res 
 q0.ro 
 True 
 4,000,000.0 ns 
 2,000.0 ns 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=0,bin_mode='average',phase=0,t0=0) 
 0 
 
 
 3 
 IdlePulse(duration=0.004)_p_0 
 None 
 cl0.baseband 
 False 
 4,002,000.0 ns 
 4,000,000.0 ns 
 IdlePulse(duration=0.004) 
 0 
 
 
 4 
 SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0 
 q0:mw 
 q0.01 
 False 
 8,002,000.0 ns 
 1,000.0 ns 
 SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0) 
 0 
 
 
 5 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=1,bin_mode='average',phase=0,t0=0)_acq_0 
 q0:res 
 q0.ro 
 True 
 8,002,000.0 ns 
 2,000.0 ns 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=1,bin_mode='average',phase=0,t0=0) 
 0 
 
 
 6 
 IdlePulse(duration=0.004)_p_0 
 None 
 cl0.baseband 
 False 
 8,004,000.0 ns 
 4,000,000.0 ns 
 IdlePulse(duration=0.004) 
 0 
 
 
 7 
 SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0 
 q0:mw 
 q0.01 
 False 
 12,004,000.0 ns 
 1,000.0 ns 
 SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0) 
 0 
 
 
 8 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=2,bin_mode='average',phase=0,t0=0)_acq_0 
 q0:res 
 q0.ro 
 True 
 12,004,000.0 ns 
 2,000.0 ns 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=2,bin_mode='average',phase=0,t0=0) 
 0

In [7]:
comp_sched.hardware_timing_table

waveform_op_id 
 port 
 clock 
 is_acquisition 
 abs_time 
 duration 
 operation 
 wf_idx 
 hardware_channel 
 clock_cycle_start 
 sample_start 
 waveform_id 
 
 
 
 
 0 
 IdlePulse(duration=0.004)_p_0 
 None 
 cl0.baseband 
 False 
 0.0 ns 
 4,000,000.0 ns 
 IdlePulse(duration=0.004) 
 0 
 None 
 nan 
 nan 
 IdlePulse(duration=0.004)_p_0_sample:nan_phase:0.0 
 
 
 2 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=0,bin_mode='average',phase=0,t0=0)_acq_0 
 q0:res 
 q0.ro 
 True 
 4,000,000.0 ns 
 2,000.0 ns 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=0,bin_mode='average',phase=0,t0=0) 
 0 
 ic_uhfqa0.awg0 
 900,000.0 
 0.0 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=*,_acq_0_sample:0.0_phase:0.0 
 
 
 1 
 SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0 
 q0:mw 
 q0.01 
 False 
 4,000,190.0 ns 
 1,000.0 ns 
 SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0) 
 0 
 ic_hdawg0.awg0 
 1,200,057.0 
 0.0 
 SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0_sample:0.0_phase:0.0 
 
 
 3 
 IdlePulse(duration=0.004)_p_0 
 None 
 cl0.baseband 
 False 
 4,002,000.0 ns 
 4,000,000.0 ns 
 IdlePulse(duration=0.004) 
 0 
 None 
 nan 
 nan 
 IdlePulse(duration=0.004)_p_0_sample:nan_phase:0.0 
 
 
 5 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=1,bin_mode='average',phase=0,t0=0)_acq_0 
 q0:res 
 q0.ro 
 True 
 8,002,000.0 ns 
 2,000.0 ns 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=1,bin_mode='average',phase=0,t0=0) 
 0 
 ic_uhfqa0.awg0 
 1,800,450.0 
 0.0 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=*,_acq_0_sample:0.0_phase:0.0 
 
 
 4 
 SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0 
 q0:mw 
 q0.01 
 False 
 8,002,190.0 ns 
 1,000.0 ns 
 SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0) 
 0 
 ic_hdawg0.awg0 
 2,400,657.0 
 0.0 
 SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0_sample:0.0_phase:0.0 
 
 
 6 
 IdlePulse(duration=0.004)_p_0 
 None 
 cl0.baseband 
 False 
 8,004,000.0 ns 
 4,000,000.0 ns 
 IdlePulse(duration=0.004) 
 0 
 None 
 nan 
 nan 
 IdlePulse(duration=0.004)_p_0_sample:nan_phase:0.0 
 
 
 8 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=2,bin_mode='average',phase=0,t0=0)_acq_0 
 q0:res 
 q0.ro 
 True 
 12,004,000.0 ns 
 2,000.0 ns 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=2,bin_mode='average',phase=0,t0=0) 
 0 
 ic_uhfqa0.awg0 
 2,700,900.0 
 0.0 
 SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=*,_acq_0_sample:0.0_phase:0.0 
 
 
 7 
 SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0 
 q0:mw 
 q0.01 
 False 
 12,004,190.0 ns 
 1,000.0 ns 
 SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0) 
 0 
 ic_hdawg0.awg0 
 3,601,257.0 
 0.0 
 SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0_sample:0.0_phase:0.0

In [8]:
comp_sched.hardware_waveform_dict

{
    "SSBIntegrationComplex(port='q0:res',clock='q0.ro',duration=2e-06,acq_channel=0,acq_index=*,_acq_0_sample:0.0_phase:0.0": array([ 1.        +1.j        ,  1.40883205+0.12325683j,
        1.15845593-0.81115958j, ..., -1.3660254 +0.3660254j ,
       -0.81115958+1.15845593j,  0.12325683+1.40883205j]),
    "SquarePulse(amp=0.05,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0_sample:0.0_phase:0.0": array([0.04873397+0.j        , 0.04705799-0.01327714j,
       0.04217509-0.02564946j, ..., 0.03450222+0.03627381j,
       0.04223463+0.02564946j, 0.04708881+0.01327714j]),
    "SquarePulse(amp=0.475,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0_sample:0.0_phase:0.0": array([0.46297273+0.j        , 0.44705092-0.1261328j ,
       0.40066333-0.24366986j, ..., 0.32777112+0.34460122j,
       0.40122896+0.24366986j, 0.44734371+0.1261328j ]),
    "SquarePulse(amp=0.9,duration=1e-06,port='q0:mw',clock='q0.01',phase=0,t0=0)_p_0_sample:0.0_phase:0.0": array([0.87721149+0.j        , 0.84704385-0.23898846j,
       0.75915158-0.46169026j, ..., 0.62104001+0.65292863j,
       0.76022329+0.46169026j, 0.84759861+0.23898846j])
}

In [9]:
comp_sched.compiled_instructions

{
    'ic_hdawg0': ZIDeviceConfig(
        name='ic_hdawg0',
        settings_builder=<quantify_scheduler.backends.zhinst.settings.ZISettingsBuilder object at 0x7fa4cfcb2070>,
        acq_config=None
    ),
    'generic': {
        'mw_qubit.ch_1.frequency': 6600000000.0,
        'mw_qubit.power': 13,
        'mw_readout.frequency': 6300000000.0,
        'mw_readout.power': 16
    },
    'ic_uhfqa0': ZIDeviceConfig(
        name='ic_uhfqa0',
        settings_builder=<quantify_scheduler.backends.zhinst.settings.ZISettingsBuilder object at 0x7fa4cfc99370>,
        acq_config=ZIAcquisitionConfig(
            n_acquisitions=3,
            resolvers={
                0: functools.partial(<function result_acquisition_resolver at 0x7fa4cff68310>, result_nodes=['qas/0/result/data/0/wave', 'qas/0/result/data/1/wave'])
            },
            bin_mode=<BinMode.AVERAGE: 'average'>
        )
    )
}

In [10]:
# the .as_dict method can be used to generate a "readable" overview of the settings.
hdawg_settings_dict = (
    comp_sched.compiled_instructions["ic_hdawg0"].settings_builder.build().as_dict()
)
# hdawg_settings_dict
hdawg_settings_dict

{
    'sigouts/*/on': 0,
    'awgs/*/single': 1,
    'system/awg/channelgrouping': 0,
    'awgs/0/time': 0,
    'awgs/1/time': 0,
    'sigouts/0/on': 1,
    'sigouts/1/on': 1,
    'awgs/0/outputs/0/gains/0': 1,
    'awgs/0/outputs/1/gains/1': 1,
    'sigouts/0/offset': -0.0542,
    'sigouts/1/offset': -0.0328,
    'sigouts/2/on': 1,
    'sigouts/3/on': 1,
    'awgs/1/outputs/0/gains/0': 1,
    'awgs/1/outputs/1/gains/1': 1,
    'sigouts/2/offset': 0.042,
    'sigouts/3/offset': 0.028,
    'awgs/0/commandtable/data': '{"header": {"version": "0.2", "partial": false}, "table": [{"index": 0, "waveform": {"index": 0, "length": 2400}}, {"index": 1, "waveform": {"index": 1, "length": 2400}}, {"index": 2, "waveform": {"index": 2, "length": 2400}}]}',
    'awgs/0/waveform/waves/0': array([1596,    0, 1541, ...,  840, 1542,  435], dtype=int16),
    'awgs/0/waveform/waves/1': array([15170,     0, 14648, ...,  7984, 14658,  4132], dtype=int16),
    'awgs/0/waveform/waves/2': array([28743,     0, 27755, ..., 15128, 27773,  7830], dtype=int16),
    'awgs/1/commandtable/data': '{"header": {"version": "0.2", "partial": false}, "table": []}',
    'compiler/sourcestring': {
        0: '// Generated by quantify-scheduler.\n// Variables\nvar __repetitions__ = 1024;\nwave w0 = placeholder(2400);\nwave w1 = placeholder(2400);\nwave w2 = placeholder(2400);\n\n// Operations\nassignWaveIndex(w0, w0, 0);\nassignWaveIndex(w1, w1, 1);\nassignWaveIndex(w2, w2, 2);\nsetTrigger(0);\t//  n_instr=1\nrepeat(__repetitions__)\n{\n  setTrigger(AWG_MARKER1 + AWG_MARKER2);\t//  n_instr=2\n  wait(1200052);\t\t// clock=2\t n_instr=3\n  executeTableEntry(0);\t// clock=1200057 pulse=0 n_instr=0\n  wait(1200597);\t\t// clock=1200057\t n_instr=3\n  executeTableEntry(1);\t// clock=2400657 pulse=1 n_instr=0\n  wait(1200597);\t\t// clock=2400657\t n_instr=3\n  executeTableEntry(2);\t// clock=3601257 pulse=2 n_instr=0\n  setTrigger(0);\t// clock=3601257 n_instr=1\n  wait(539);\t\t// clock=3601258, dead time to ensure total schedule duration\t n_instr=3\n}\n',
        1: '// Generated by quantify-scheduler.\n// Variables\nvar __repetitions__ = 1024;\n\n// Operations\nsetTrigger(0);\t//  n_instr=1\nrepeat(__repetitions__)\n{\n  setTrigger(AWG_MARKER1 + AWG_MARKER2);\t//  n_instr=2\n  setTrigger(0);\t// clock=2 n_instr=1\n  wait(3601794);\t\t// clock=3, dead time to ensure total schedule duration\t n_instr=3\n}\n'
    }
}

In [11]:
awg_index = 0
print(hdawg_settings_dict["compiler/sourcestring"][awg_index])

// Generated by quantify-scheduler.
// Variables
var __repetitions__ = 1024;
wave w0 = placeholder(2400);
wave w1 = placeholder(2400);
wave w2 = placeholder(2400);

// Operations
assignWaveIndex(w0, w0, 0);
assignWaveIndex(w1, w1, 1);
assignWaveIndex(w2, w2, 2);
setTrigger(0);	//  n_instr=1
repeat(__repetitions__)
{
  setTrigger(AWG_MARKER1 + AWG_MARKER2);	//  n_instr=2
  wait(1200052);		// clock=2	 n_instr=3
  executeTableEntry(0);	// clock=1200057 pulse=0 n_instr=0
  wait(1200597);		// clock=1200057	 n_instr=3
  executeTableEntry(1);	// clock=2400657 pulse=1 n_instr=0
  wait(1200597);		// clock=2400657	 n_instr=3
  executeTableEntry(2);	// clock=3601257 pulse=2 n_instr=0
  setTrigger(0);	// clock=3601257 n_instr=1
  wait(539);		// clock=3601258, dead time to ensure total schedule duration	 n_instr=3
}



In [12]:
# the .as_dict method can be used to generate a "readable" overview of the settings.
uhfqa_settings_dict = (
    comp_sched.compiled_instructions["ic_uhfqa0"].settings_builder.build().as_dict()
)
# uhfqa_settings_dict
uhfqa_settings_dict

{
    'awgs/0/single': 1,
    'qas/0/rotations/*': (1+1j),
    'qas/0/integration/sources/*': 0,
    'sigouts/0/on': 1,
    'sigouts/1/on': 1,
    'awgs/0/time': 0,
    'qas/0/integration/weights/0/real': array([1.        , 1.40883205, 1.15845593, ..., 0.        , 0.        ,
       0.        ]),
    'qas/0/integration/weights/1/real': array([ 1.        ,  0.12325683, -0.81115958, ...,  0.        ,
        0.        ,  0.        ]),
    'qas/0/integration/weights/2/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/3/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/4/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/5/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/6/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/7/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/8/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/9/real': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/0/imag': array([ 1.        ,  0.12325683, -0.81115958, ...,  0.        ,
        0.        ,  0.        ]),
    'qas/0/integration/weights/1/imag': array([-1.        , -1.40883205, -1.15845593, ..., -0.        ,
       -0.        , -0.        ]),
    'qas/0/integration/weights/2/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/3/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/4/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/5/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/6/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/7/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/8/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'qas/0/integration/weights/9/imag': array([0., 0., 0., ..., 0., 0., 0.]),
    'sigouts/0/offset': 0.0,
    'sigouts/1/offset': 0.0,
    'awgs/0/waveform/waves/0': array([23258, 23258, 32766, ..., 26943,  2866, 32766], dtype=int16),
    'qas/0/integration/mode': 0,
    'qas/0/integration/length': 3600,
    'qas/0/result/enable': 1,
    'qas/0/monitor/enable': 0,
    'qas/0/delay': 0,
    'qas/0/result/mode': 0,
    'qas/0/result/source': 7,
    'qas/0/result/length': 3,
    'qas/0/result/averages': 1024,
    'qas/0/result/reset': 1,
    'qas/0/monitor/reset': 1,
    'compiler/sourcestring': {
        0: '// Generated by quantify-scheduler.\n// Variables\nvar __repetitions__ = 1024;\nwave w0 = "ic_uhfqa0_awg0_wave0";\n\n// Operations\nrepeat(__repetitions__)\n{\n  waitDigTrigger(2, 1);\t// \t// clock=0\n  wait(900000);\t\t// clock=0\t n_instr=900000\n  startQA(QA_INT_ALL, true);\t// clock=900000 n_instr=7\n  wait(900443);\t\t// clock=900007\t n_instr=900443\n  startQA(QA_INT_ALL, true);\t// clock=1800450 n_instr=7\n  wait(900443);\t\t// clock=1800457\t n_instr=900443\n  startQA(QA_INT_ALL, true);\t// clock=2700900 n_instr=7\n}\n'
    }
}

In [13]:
awg_index = 0
print(uhfqa_settings_dict["compiler/sourcestring"][awg_index])

// Generated by quantify-scheduler.
// Variables
var __repetitions__ = 1024;
wave w0 = "ic_uhfqa0_awg0_wave0";

// Operations
repeat(__repetitions__)
{
  waitDigTrigger(2, 1);	// 	// clock=0
  wait(900000);		// clock=0	 n_instr=900000
  startQA(QA_INT_ALL, true);	// clock=900000 n_instr=7
  wait(900443);		// clock=900007	 n_instr=900443
  startQA(QA_INT_ALL, true);	// clock=1800450 n_instr=7
  wait(900443);		// clock=1800457	 n_instr=900443
  startQA(QA_INT_ALL, true);	// clock=2700900 n_instr=7
}



In [14]:
from quantify_scheduler.schedules.verification import acquisition_staircase_sched

acq_channel = 0
schedule = acquisition_staircase_sched(
    readout_pulse_amps=np.linspace(0, 1, 4),
    readout_pulse_duration=1e-6,
    readout_frequency=6e9,
    acquisition_delay=100e-9,
    integration_time=2e-6,
    port="q0:res",
    clock="q0.ro",
    repetitions=1024,
    acq_channel=acq_channel,
)


comp_sched = qcompile(
    schedule, device_cfg=transmon_device_cfg, hardware_cfg=zhinst_hardware_cfg
)